<a href="https://colab.research.google.com/github/rosemilca-Ing/machine_learning_I/blob/big_data/Projet_Big_DATA_TP_2_sur_Apache_Spark.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **TP 2 sur Apache Spark**

## **1. Objectifs**
Le TP consiste à regrouper des documents textuels tels que les documents qui
partagent le même thème se retrouvent dans le même groupe, et les documents qui
portent sur des sujets très différents se trouvent dans des groupes différents.

Réalisé par Rose-Milca CENAT et Anis Soufiane HAOUA

## **2. Mise en place de l’environnement de travail**


### **1. Créer un notebook sur Google Colab**

### **2. Installer Spark**

In [ ]:
# install Java8
!apt-get install openjdk-8-jdk-headless -qq > /dev/null

! wget -q https://dlcdn.apache.org/spark/spark-3.2.3/spark-3.2.3-bin-hadoop3.2.tgz
! tar xf /content/spark-3.2.3-bin-hadoop3.2.tgz


# # install findspark
!pip install -q findspark
!pip install pyspark

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-3.2.3-bin-hadoop3.2"

import findspark

findspark.init("spark-3.2.3-bin-hadoop3.2")

### **3. Valeur de la variable d'environnement PYSPARK_SUBMIT_ARGS**

In [ ]:
import os
os.environ['PYSPARK_SUBMIT_ARGS'] = '--packages org.apache.spark:spark-avro_2.11:2.4.5 pyspark-shell'


### **4. Créer un objet SparkContext**


In [ ]:
from pyspark import SparkContext, SparkConf

configuration = SparkConf().setAppName("myappdocuments").setMaster("local[4]")
sc = SparkContext(conf=configuration)

ValueError: ignored

### **5. Créer un objet de type SparkSession**.

In [ ]:
from pyspark.sql import SparkSession

spark = SparkSession.builder.config(conf=configuration).getOrCreate()


## **3. Données**

### **1. Télécharger des données textuelles**

In [ ]:
! wget -q http://qwone.com/~jason/20Newsgroups/20news-19997.tar.gz

### **2. Décompresser les données**


In [ ]:
! tar xf /content/20news-19997.tar.gz

### **3. Charger les données dans deux variables de type RDD**

In [ ]:
rddAtheism = sc.wholeTextFiles("20_newsgroups/alt.atheism/")

In [ ]:
#Affichage des éléments du rdd rddAtheism
rddElements=rddAtheism.collect()

for e in rddElements:
 print("Element key : "+e[0]+ "\nElement value : "+e[1])

Element key : file:/content/20_newsgroups/alt.atheism/53791
Element value : Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:53791 talk.religion.misc:84109 talk.origins:41079
Newsgroups: alt.atheism,talk.religion.misc,talk.origins
Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!bb3.andrew.cmu.edu!news.sei.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!zaphod.mps.ohio-state.edu!swrinde!cs.utexas.edu!utnut!torn!nott!cunews!rjg
From: rjg@doe.carleton.ca (Richard Griffith)
Subject: Re: Burden of Proof
Message-ID: <rjg.735427215@wesley>
Sender: news@cunews.carleton.ca (News Administrator)
Organization: Dept. of Electronics, Carleton University
References: <C5t5sF.8oz@mentor.cc.purdue.edu> <1r4b59$7hg@aurora.engr.LaTech.edu>
Date: Wed, 21 Apr 1993 21:20:15 GMT
Lines: 23

In <1r4b59$7hg@aurora.engr.LaTech.edu> ray@engr.LaTech.edu (Bill Ray) writes:

>If I make a statement, "That God exists, loves me, etc." but in no way
>insist that you believe it, does that place a 

In [ ]:
rddBaseball = sc.wholeTextFiles("20_newsgroups/rec.sport.baseball/")

In [ ]:
#Affichage des éléments du rdd rddBaseball
rddElements1=rddBaseball.collect()
for e in rddElements1:
 print("Element key : "+e[0]+"\n"+ "Element value : "+e[1])

Element key : file:/content/20_newsgroups/rec.sport.baseball/104985
Element value : Newsgroups: rec.sport.baseball
Path: cantaloupe.srv.cs.cmu.edu!rochester!udel!gatech!howland.reston.ans.net!zaphod.mps.ohio-state.edu!magnus.acs.ohio-state.edu!dmoney
From: dmoney@magnus.acs.ohio-state.edu (Dean R Money)
Subject: The Braves will come around...
Message-ID: <1993Apr23.193027.26515@magnus.acs.ohio-state.edu>
Sender: news@magnus.acs.ohio-state.edu
Nntp-Posting-Host: bottom.magnus.acs.ohio-state.edu
Organization: The Ohio State University
Date: Fri, 23 Apr 1993 19:30:27 GMT
Lines: 28

To all the Braves doubters:

Don't worry.  The bats will come alive, and the Braves will come around.
The pitching is solid, and as long the Braves don't have serious injuries
to the starting rotation, they'll continue to pitch well.  Heck, with
the five starters on the Braves rotation, they could even sustain an
injury to one of the five (I hope this doesn't happen, though).

The bats are there... Pendleton wi

### **4. Séparer le corps du message de l’entête. (séparation sur “\n\n” ?)**

In [ ]:
#Séparation Rdd rddAtheism
rddsepAtheism = rddAtheism.map(lambda x : (x[1].split("\n\n",1)[0], x[1].split("\n\n",1)[1]))


In [ ]:
#Séparation Rdd rddBaseball
rddsepBaseball = rddBaseball.map(lambda x : (x[1].split("\n\n",1)[0], x[1].split("\n\n",1)[1]))

In [ ]:
#Entete Message rddAtheism
enteteAtheism=rddsepAtheism.keys()
rddElements=enteteAtheism.collect()
for e in rddElements:
  print("\n\n***********************************\nEntete Message rdd rddAtheism \n***********************************\n",e)

Le flux de sortie a été tronqué et ne contient que les 5000 dernières lignes.
Newsgroups: alt.atheism
Subject: Re: After 2000 years, can we say that Christian Morality is
Message-ID: <930416.134733.3c8.rusnews.w165w@mantis.co.uk>
Date: Fri, 16 Apr 1993 13:47:33 +0100
References: <1qie61$fkt@horus.ap.mchp.sni.de> <1993Apr15.125245.12872@abo.fi> <1qkq9t$66n@horus.ap.mchp.sni.de>
Organization: Mantis Consultants, Cambridge. UK.
X-Newsreader: rusnews v1.01
Lines: 13


***********************************
Entete Message rdd rddAtheism 
***********************************
 Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!zaphod.mps.ohio-state.edu!wupost!uunet!pipex!ibmpcug!mantis!news
From: mathew <mathew@mantis.co.uk>
Newsgroups: alt.atheism
Subject: Re: Gulf War (was Re: Death Penalty was Re: Political Atheists?)
Message-ID: <930421.120012.2o5.rusnews.w165w@mantis.co.uk>
Date: Wed, 21 Apr 1993 12:00:12 +0100
References: <1

In [ ]:
#Corps rddAtheism
corpsAtheism=rddsepAtheism.values()
rddElements=corpsAtheism.collect()
for e in rddElements:
  print("\n\n***********************************\nCorps Message rdd rddAtheism \n***********************************\n",e)


In [ ]:
#Entete rddBaseball
enteteBaseball=rddsepBaseball.keys()
rddElements=enteteBaseball.collect()
for e in rddElements:
  print("\n\n***********************************\nEntete Message rdd rddBaseball \n***********************************\n",e)

In [ ]:
#Corps rddBaseball
corpsBaseball=rddsepBaseball.values()
rddElements=corpsBaseball.collect()
for e in rddElements:
  print("\n\n***********************************\nCorps Message rdd rddBaseball \n***********************************\n",e)


### **5. Extraire quelques champs de l’entête**

La fonction extract_header_fields prend en entrée le texte d'un document et renvoie un tuple contenant les valeurs des champs "Newsgroups" et "Organization" de l'entête. La fonction utilise des expressions régulières pour extraire les valeurs de ces champs.

Finalement, les résultats sont affichés en utilisant la méthode take pour afficher les 10 premiers documents de chaque RDD.

In [ ]:
import re

# Fonction pour extraire les champs de l'entête
def extract_header_fields(text):
    # Recherche du champ "Newsgroups"
    newsgroups_match = re.search(r"Newsgroups:\s+(.*)", text)
    if newsgroups_match:
        newsgroups = newsgroups_match.group(1)
    else:
        newsgroups = None

    # Recherche du champ "Organization"
    org_match = re.search(r"Organization:\s+(.*)", text)
    if org_match:
        organization = org_match.group(1)
    else:
        organization = None

    return (newsgroups, organization)

# Extraction des champs de l'entête pour rddBaseball
header_fields_baseball = rddBaseball.map(lambda x: extract_header_fields(x[1]))

# Extraction des champs de l'entête pour rddAtheism
header_fields_atheism = rddAtheism.map(lambda x: extract_header_fields(x[1]))

# Affichage des résultats
print("Les champs des entetes du baseball")
print(header_fields_baseball.take(5)) # Affichage des 5 premiers documents
print("Les champs des entetes de l'atheism")
print(header_fields_atheism.take(5)) # Affichage des 5 premiers documents

### **6. Fusionner les deux RDD**

In [ ]:
rddfusion = rddAtheism.union(rddBaseball)

In [ ]:
#Affichage des éléments du rdd rddfusion
rddfusionElements=rddfusion.collect()
for e in rddfusionElements:
 print("Element key : "+e[0]+"\n"+ "Element value : "+e[1])

### **7. Transformer le nouveau RDD obtenu : pyspark.sql.Row**

In [ ]:
from pyspark.sql import Row
rowrdd = rddfusion.map(lambda x: Row(x[0], x[1]))

### **8. Créer un objet de type DataFrame à partir du RDD précédent**


In [ ]:
from pyspark.sql import Row
deptColumns = ["file","contents"]
deptDF = spark.createDataFrame(rowrdd, schema=deptColumns)



### **9. Sauvegarder la DataFrame au format Avro**

In [ ]:
!pip install pandavro

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 28.1 MB/s eta 0:00:00
  Created wheel for pandavro: filename=pandavro-1.7.1-py3-none-any.whl size=5688 sha256=85005a18619e3952c193c96aea3d1e9bd867f1e982c5187f15e5f0ecfb40a76d
  Stored in directory: /root/.cache/pip/wheels/85/cc/15/480a3cfa1a9fc49e2af9bde7437bd6c8c0265f17e61f32672b
Successfully built pandavro


In [ ]:

pandasDF = deptDF.toPandas()
pandasDF

file  \
0         file:/content/20_newsgroups/alt.atheism/53791   
1         file:/content/20_newsgroups/alt.atheism/54220   
2         file:/content/20_newsgroups/alt.atheism/51127   
3         file:/content/20_newsgroups/alt.atheism/54191   
4         file:/content/20_newsgroups/alt.atheism/51225   
...                                                 ...   
1995  file:/content/20_newsgroups/rec.sport.baseball...   
1996  file:/content/20_newsgroups/rec.sport.baseball...   
1997  file:/content/20_newsgroups/rec.sport.baseball...   
1998  file:/content/20_newsgroups/rec.sport.baseball...   
1999  file:/content/20_newsgroups/rec.sport.baseball...   

                                               contents  
0     Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:53...  
1     Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....  
2     Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....  
3     Path: cantaloupe.srv.cs.cmu.edu!das-news.harva...  
4     Newsgroups: alt.atheism\nPath: cantaloupe.srv....  
...                                                 ...  
1995  Newsgroups: rec.sport.baseball\nPath: cantalou...  
1996  Newsgroups: rec.sport.baseball\nPath: cantalou...  
1997  Path: cantaloupe.srv.cs.cmu.edu!rochester!udel...  
1998  Path: cantaloupe.srv.cs.cmu.edu!das-news.harva...  
1999  Newsgroups: rec.sport.baseball\nPath: cantalou...  

[2000 rows x 2 columns]

In [ ]:
import pandavro as pdx
filename_avro = "deptDF.avro"

pdx.to_avro(filename_avro, pandasDF)

In [ ]:
!ls -lh

total 309M
-rw-r--r--  1 root  root   17M Sep 22  2014 20news-19997.tar.gz
drwxr-xr-x 22 28757 staff 4.0K Apr  3  1999 20_newsgroups
-rw-r--r--  1 root  root  4.3M Mar  6 21:53 deptDF.avro
drwxr-xr-x  1 root  root  4.0K Mar  3 14:33 sample_data
drwxr-xr-x 13   501  1000 4.0K Nov 14 17:54 spark-3.2.3-bin-hadoop3.2
-rw-r--r--  1 root  root  288M Nov 14 18:47 spark-3.2.3-bin-hadoop3.2.tgz


In [ ]:
saved = pdx.read_avro(filename_avro)
print(saved)

                                                   file  \
0         file:/content/20_newsgroups/alt.atheism/53791   
1         file:/content/20_newsgroups/alt.atheism/54220   
2         file:/content/20_newsgroups/alt.atheism/51127   
3         file:/content/20_newsgroups/alt.atheism/54191   
4         file:/content/20_newsgroups/alt.atheism/51225   
...                                                 ...   
1995  file:/content/20_newsgroups/rec.sport.baseball...   
1996  file:/content/20_newsgroups/rec.sport.baseball...   
1997  file:/content/20_newsgroups/rec.sport.baseball...   
1998  file:/content/20_newsgroups/rec.sport.baseball...   
1999  file:/content/20_newsgroups/rec.sport.baseball...   

                                               contents  
0     Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:53...  
1     Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....  
2     Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....  
3     Path: cantaloupe.srv.cs.cmu.edu!das-news.harva...  
4

### **10. Sauvegarder la DataFrame au format Parquet**

In [ ]:
!pip install pyarrow

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import pyarrow as pa
import pyarrow.parquet as pq

filename_parquet = 'deptDF.parquet'

table = pa.Table.from_pandas(pandasDF)
pq.write_table(table, filename_parquet)

In [ ]:
table2 = pq.read_table(filename_parquet)
print(table2)

pyarrow.Table
file: string
contents: string
----
file: [["file:/content/20_newsgroups/alt.atheism/53791","file:/content/20_newsgroups/alt.atheism/54220","file:/content/20_newsgroups/alt.atheism/51127","file:/content/20_newsgroups/alt.atheism/54191","file:/content/20_newsgroups/alt.atheism/51225",...,"file:/content/20_newsgroups/rec.sport.baseball/104882","file:/content/20_newsgroups/rec.sport.baseball/104711","file:/content/20_newsgroups/rec.sport.baseball/104672","file:/content/20_newsgroups/rec.sport.baseball/102681","file:/content/20_newsgroups/rec.sport.baseball/104937"]]
contents: [["Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:53791 talk.religion.misc:84109 talk.origins:41079
Newsgroups: alt.atheism,talk.religion.misc,talk.origins
Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!bb3.andrew.cmu.edu!news.sei.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!zaphod.mps.ohio-state.edu!swrinde!cs.utexas.edu!utnut!torn!nott!cunews!rjg
From: rjg@doe.carleton.ca

## **4. Analyse descriptive**

Faire une analyse descriptive de la DataFrame obtenue à l’étape précédente (API Spark
SQL) :

Voici l'analyse descriptive de la DataFrame df_header obtenue à partir des champs extraits des entêtes des documents :

### **1. Vérifier qu’on a bien deux catégories différentes de documents**

Vérification des catégories différentes de documents :

Pour vérifier qu'on a bien deux catégories différentes de documents, on peut utiliser la méthode distinct() pour afficher les valeurs distinctes de la colonne "newsgroups" :


In [ ]:
# Fusion des ENTETES des deux RDD
header_fields = header_fields_atheism.union(header_fields_baseball)

# Transformation en objets Row
rows = header_fields.map(lambda x: Row(newsgroups=x[0], organization=x[1]))

# Création du DataFrame
df_header = rows.toDF()

# Et enfin, affichage du df
df_header.show()

+--------------------+--------------------+
|          newsgroups|        organization|
+--------------------+--------------------+
|alt.atheism,talk....|Dept. of Electron...|
|         alt.atheism|Case Western Rese...|
|         alt.atheism|California Instit...|
|         alt.atheism|Decision Support ...|
|         alt.atheism|Welch Medical Lib...|
|         alt.atheism|                null|
|         alt.atheism|Decision Support ...|
|         alt.atheism|                null|
|sci.skeptic,alt.a...|University of Mar...|
|alt.atheism,talk....|  Indiana University|
|         alt.atheism|  Siemens-Nixdorf AG|
|         alt.atheism|                 sgi|
|         alt.atheism|                 sgi|
|         alt.atheism|Decision Support ...|
|         alt.atheism|Monash University...|
|         alt.atheism|California Instit...|
|         alt.atheism|ITC, Griffith Uni...|
|         alt.atheism|                null|
|         alt.atheism|Technical Univers...|
|         alt.atheism|Tektronix 

In [ ]:
from pyspark.sql.functions import col
# Filtrer le DataFrame pour ne garder que les catégories recherchées
df = df_header.filter(col("newsgroups").isin(["alt.atheism", "rec.sport.baseball"]))

# Afficher le nombre de catégories distinctes
print(df.select('newsgroups').distinct().count())

2


On obtient la valeur 2, ce qui confirme qu'on a bien deux catégories différentes de documents.


In [ ]:
 print(df.select("newsgroups").distinct().show())

+------------------+
|        newsgroups|
+------------------+
|       alt.atheism|
|rec.sport.baseball|
+------------------+

None


### **2. Donner le nombre d'organisations différentes**


In [ ]:
print(df.groupBy("organization").count().show())


+--------------------+-----+
|        organization|count|
+--------------------+-----+
|Brownian Motion Inc.|    1|
|Software Engineer...|    4|
|Department of Com...|    2|
|University of Was...|    8|
|California Instit...|   63|
|Kupajava, East of...|    8|
|California State ...|    1|
|       Cursed Female|    1|
|Salvation Army Dr...|    3|
|Johns Hopkins Uni...|    3|
|University Of Alb...|    1|
|The Loyal Order O...|    1|
|Mantis Consultant...|   18|
|Louisiana Tech Un...|    2|
|Nyx, Public Acces...|    6|
|Penn State Univer...|   12|
|Society for Putti...|    7|
|Supercomputer Com...|    1|
|South Australian ...|    2|
|Nottingham Univer...|    6|
+--------------------+-----+
only showing top 20 rows

None


In [ ]:
df.groupBy('organization').count().count()

431

### **3. Suivant les champs extraits à la partie 3, donner d’autres statistiques descriptives (nombre, moyenne, etc)**

On peut utiliser la fonction groupBy() et différentes fonctions d'agrégation (count(), mean(), min(), max(), etc.) pour donner des statistiques descriptives sur les champs extraits.

Par exemple, Pour le champ "Organization", on peut utiliser la fonction groupBy() et la fonction count() pour compter le nombre de documents pour chaque organisation.


In [ ]:
df.groupBy('organization').count().show()


Nombre de documents par catégorie et par organisation :

In [ ]:
df.groupBy("newsgroups", "organization").count().show()

Catégorie la plus fréquente (Mode):

In [ ]:
from pyspark.sql.functions import avg, desc
df.groupBy("newsgroups").count().orderBy(desc("count")).first()["newsgroups"]

'rec.sport.baseball'

Organisation la plus fréquente (Mode):

In [ ]:
df.groupBy("organization").count().orderBy(desc("count")).first()["organization"]

'California Institute of Technology, Pasadena'

## **5. Transformation du texte**


### **1. Consulter la page (API MlLib) :**



In [ ]:
!https://spark.apache.org/docs/latest/ml-features.html#feature-extractors

/bin/bash: https://spark.apache.org/docs/latest/ml-features.html#feature-extractors: No such file or directory


### **2. Découper les documents en listes de mots à l’aide de Tokenizer**


In [ ]:
from pyspark.ml.feature import HashingTF, IDF, Tokenizer


In [ ]:

deptdftokenizer = Tokenizer(inputCol="contents", outputCol="words")
wordsDF = deptdftokenizer.transform(deptDF)

In [ ]:
wordsDF.select('words').show(truncate=False)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

### **3. Créer une représentation vectorielle des documents à l’aide de HashingTF**


In [ ]:
deptdfhashingTF = HashingTF(inputCol="words", outputCol="features", numFeatures=20)
featurizedData = deptdfhashingTF.transform(wordsDF)

In [ ]:
featurizedData.select('features').show(truncate=False)

+------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|features                                                                                                                                                          |
+------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|(20,[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19],[14.0,9.0,10.0,25.0,8.0,9.0,7.0,8.0,17.0,8.0,9.0,6.0,15.0,9.0,14.0,13.0,13.0,8.0,14.0,6.0])               |
|(20,[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19],[7.0,4.0,8.0,13.0,14.0,7.0,12.0,4.0,8.0,9.0,4.0,7.0,99.0,16.0,7.0,20.0,8.0,10.0,5.0,6.0])                 |
|(20,[0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19],[7.0,5.0,5.0,8.0,6.0,7.0,6.0,7.0,3.0,7.0,3.0,5.0,18.0,7.0,5.0,11.0,5.0,13.0,8.0,6.0])                     |
|(20,[0,1,

##**6. Grouper les documents qui ont des représentations vectorielles proches**


### **1. Consulter la page :**


In [ ]:
!https://spark.apache.org/docs/latest/ml-clustering.html

/bin/bash: https://spark.apache.org/docs/latest/ml-clustering.html: No such file or directory



### **2. Utiliser l’algorithme KMeans avec un nombre du cluster égal à 2 (pour essayer de retrouver les 2 catégories qu’on a)**

In [ ]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator

# Loads data.
data= featurizedData.select('features')

# Trains a k-means model.
kmeans = KMeans().setK(2).setSeed(1)
model = kmeans.fit(data)


In [ ]:

# Make predictions
predictions = model.transform(data)

# Evaluate clustering by computing Categorie score
evaluator = ClusteringEvaluator()

Categorie = evaluator.evaluate(predictions)
print("Categorie with squared euclidean distance = " + str(Categorie))

# Shows the result.
categories = model.clusterCenters()
print("Cluster categories: \n")
for category in categories:
    print("**************category***************\n",category, "\n")

Categorie with squared euclidean distance = 0.991921314762465
Cluster categories: 

**************category***************
 [19.30070281 12.39608434 10.99949799 20.68574297 14.04116466 15.32781124
 14.9252008  14.33785141 17.28915663 17.5060241  10.73795181 14.6064257
 63.37349398 14.01455823 10.18273092 18.04819277 15.54869478 20.4437751
 10.16616466 13.24698795] 

**************category***************
 [ 111.875  101.25    75.5    129.625   87.5    109.75   106.75   106.25
  137.375  110.375   77.5    113.25  2394.5     84.875   69.625  144.75
   86.75   177.75    71.      84.375] 



## **7. Pour aller plus loin (optionnel)**


### **1. Pondérer les mots avec la formule Tf-Idf (avant KMeans)**


In [ ]:
idf = IDF(inputCol="features", outputCol="features_idf")
idfModel = idf.fit(featurizedData)
#Afficher

###**2. Normaliser les vecteurs représentant les documents (avant KMeans).**

In [ ]:
rescaledData = idfModel.transform(featurizedData)

rescaledData.select("words", "features").show()

+--------------------+--------------------+
|               words|            features|
+--------------------+--------------------+
|[xref:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[newsgroups:, alt...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[xref:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[xref:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[newsgroups:, alt...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[newsgroups:, alt...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2,3,4,5,...|
|[newsgroups:, alt...|(20,[0,1,2,3,4,5,...|
|[path:, cantaloup...|(20,[0,1,2

# CONCLUSION

L'utilisation de l'algorithme KMeans sur des documents textuels peut permettre de regrouper les documents qui partagent des thèmes similaires dans des groupes distincts. Cela peut être utile pour la catégorisation automatique de grands ensembles de documents.

Cependant, il est important de noter que la qualité du regroupement dépend de plusieurs facteurs, tels que la représentation des documents, la pondération des termes, le choix du nombre de clusters, etc. De plus, le regroupement des documents ne garantit pas nécessairement que tous les documents d'un groupe partagent exactement le même thème ou qu'ils ne sont pas similaires à des documents d'autres groupes.

En fin de compte, l'évaluation de la qualité du regroupement et la décision de l'utiliser ou non pour une tâche particulière dépendent des exigences et des objectifs de cette tâche.